In [1]:
#Install required packages
!pip install torch==2.5.1
!pip install transformers datasets accelerate bitsandbytes
!pip install unsloth
!pip install peft

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 363.4/363.4 MB 2.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 13.8/13.8 MB 13.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 24.6/24.6 MB 17.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 883.7/883.7 kB 14.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 664.8/664.8 MB 2.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 211.5/211.5 MB 3.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 56.3/56.3 MB 10.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 127.9/127.9 MB 7.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 207.5/207.5 MB 6.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 21.1/21.1 MB 74.4 MB/s eta 0:00:00
  Attempting uninstall: nvidia-nvjitlink-cu12
    Found existing installation: nvidia-nvjitlink-cu12 12.5.82
    Uninstalling nvidia-nvjitlink-cu12-12.5.82:
      Successfully uninstalled nvidia-nvjitlin

In [1]:
#import the necessary libraries
import torch
from datasets import Dataset
from transformers import AutoModelForCausalLM, AutoTokenizer
import pandas as pd
from datetime import datetime
from transformers import TrainingArguments, Trainer

# Verify GPU
print(f"CUDA Available: {torch.cuda.is_available()}")
if torch.cuda.is_available():
    print(f"GPU Device: {torch.cuda.get_device_name(0)}")


CUDA Available: False


In [2]:
tokenizer = AutoTokenizer.from_pretrained("TinyLlama/TinyLlama-1.1B-Chat-v1.0")
# Use AutoModelForCausalLM for decoder-only models like Llama
model = AutoModelForCausalLM.from_pretrained("TinyLlama/TinyLlama-1.1B-Chat-v1.0")

/usr/local/lib/python3.11/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


In [3]:
#Install Hugging Face Hub
!pip install huggingface_hub

In [4]:
from huggingface_hub import notebook_login

notebook_login()

In [5]:
from datasets import load_dataset

# Load the dataset from Hugging Face Hub
dataset = load_dataset("fathimazulaikha/SAWiT-Tamil-Colloquial-Dataset", data_files="my_tamil_english_dataset.csv", split="train")  # Assuming the CSV is in the "train" split

In [6]:
# Adjust max_length in the preprocessing function
def preprocess_function(examples):
    inputs = [ex for ex in examples["English Text"]]
    targets = [ex for ex in examples["Tamil Text"]]
    model_inputs = tokenizer(inputs, max_length=64, truncation=True, padding="max_length")  # Reduced max_length
    labels = tokenizer(targets, max_length=64, truncation=True, padding="max_length")  # Reduced max_length
    model_inputs["labels"] = labels["input_ids"]
    return model_inputs

tokenized_datasets = dataset.map(preprocess_function, batched=True)

In [7]:
# Split the dataset into train and test sets
tokenized_datasets = tokenized_datasets.train_test_split(test_size=0.2) # Adjust test_size as needed

In [8]:
# Ensure the data is loaded properly
print(tokenized_datasets['train'][0])
print(tokenized_datasets['train'][4])

{'English Text': 'Please complete this.', 'Tamil Text': 'Dayaavu seithu idhai mudichidunga.\t', 'Category': 'Formal Phrases\n', 'input_ids': [1, 3529, 4866, 445, 29889, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2], 'attention_mask': [1, 1, 1, 1, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0], 'labels': [1, 8373, 29874, 485, 29884, 409, 389, 29884, 1178, 23535, 17439, 436, 333, 686, 29874, 29889, 12, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2]}
{'English Text': 'Thank you very much, your help was very useful.', 'Tamil Text': 'Romba nandri, ungaloda help romba useful ah irundhuchu.\t', 'Category': 'Formal Phrases\n', 'input_ids': [1

In [9]:
import gc

# Before starting training
gc.collect()
torch.cuda.empty_cache()

In [ ]:
training_args = TrainingArguments(
    output_dir="./results",
    per_device_train_batch_size=2,  # Reduced batch size further
    per_device_eval_batch_size=2,  # Reduced batch size further
    num_train_epochs=3,
    gradient_accumulation_steps=8,  # Increased gradient accumulation further
    report_to="none",
    fp16=True,
    gradient_checkpointing=True,
)

# Initialize the Trainer with the model and training arguments
trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=tokenized_datasets["train"],  # Provide the training dataset
    eval_dataset=tokenized_datasets["test"]   # Provide the evaluation dataset
)

# Before starting training
torch.cuda.empty_cache()

# Start training
trainer.train()


`use_cache=True` is incompatible with gradient checkpointing. Setting `use_cache=False`.


In [ ]:
# Some sample English inputs for testing
english_sentences = [
    "What are you doing?",
    "What is your name?",
    "Please wait for a moment.",
    "He's such a fool.",
]

In [1]:
print(tokenizer("What are you doing?"))
print(tokenizer("enna panra?"))  # Or the expected Tanglish translation

NameError: name 'tokenizer' is not defined

In [44]:
for sentence in english_sentences:
    inputs = tokenizer(sentence, return_tensors="pt").to(model.device) # Move inputs to the same device as the model

    # Remove num_beams, num_return_sequences to use defaults
    # The error occurs because 'past_key_values' might not have the expected values during beam search.
    # Force model to not use past key values for each sentence to avoid the error.
    translated_tokens = model.generate(**inputs, use_cache=False)
    translated_text = tokenizer.decode(translated_tokens[0], skip_special_tokens=True)
    print(f"English: {sentence}")
    print(f"Tamil: {translated_text}")
    print("-" * 20)  # Separator for clarity

/usr/local/lib/python3.11/dist-packages/torch/utils/checkpoint.py:87: UserWarning: None of the inputs have requires_grad=True. Gradients will be None
  warnings.warn(


OutOfMemoryError: CUDA out of memory. Tried to allocate 22.00 MiB. GPU 0 has a total capacity of 14.74 GiB of which 6.12 MiB is free. Process 2300 has 14.73 GiB memory in use. Of the allocated memory 14.27 GiB is allocated by PyTorch, and 336.85 MiB is reserved by PyTorch but unallocated. If reserved but unallocated memory is large try setting PYTORCH_CUDA_ALLOC_CONF=expandable_segments:True to avoid fragmentation.  See documentation for Memory Management  (https://pytorch.org/docs/stable/notes/cuda.html#environment-variables)